# Part 1: segmenting the cities in neighborhoods

Packages required

In [26]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json
from geopy.geocoders import Nominatim
from pandas.io.json import json_normalize

import matplotlib.cm as cm
import matplotlib.colors as colors

from bs4 import BeautifulSoup
import requests

from sklearn.neighbors import KNeighborsClassifier

import folium

chicago neighborhoods

In [27]:
chicago_url = 'https://en.wikipedia.org/wiki/List_of_neighborhoods_in_Chicago'
source = requests.get(chicago_url).text
soup = BeautifulSoup(source, 'lxml')
table = soup.find('table')
body = table.find('tbody')
tsas = []
for tsa in table.find_all('tr'):
    tsas.append (tsa.get_text().splitlines()[1])
tsas = tsas [1:]
labels = ['Neighborhood']
chicago_neighborhoods = pd.DataFrame (tsas, columns=labels)

import geocoder
Latitudes=[]
Longitudes=[]
for i in range(chicago_neighborhoods.shape[0]):
    arg='{}, Chicago, Illinois'.format(chicago_neighborhoods.loc[i,'Neighborhood'])
    geopoint = geocoder.arcgis(arg)
    Latitudes.append(geopoint.latlng[0])
    Longitudes.append(geopoint.latlng[1])
    
chicago_neighborhoods['Latitude']=Latitudes
chicago_neighborhoods['Longitude']=Longitudes

ny neighborhoods

In [28]:
with open('ny_neighborhoods.json') as json_data:
    newyork_data = json.load(json_data)
neighborhoods_data = newyork_data['features']
ny_neighborhoods = pd.DataFrame(columns=['Neighborhood', 'Latitude', 'Longitude'])
for data in neighborhoods_data:
    neighborhood_name = data['properties']['name']
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    ny_neighborhoods = ny_neighborhoods.append({'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [31]:
ny_neighborhoods

Neighborhood   Latitude  Longitude
0                    Wakefield  40.894705 -73.847201
1                   Co-op City  40.874294 -73.829939
2                  Eastchester  40.887556 -73.827806
3                    Fieldston  40.895437 -73.905643
4                    Riverdale  40.890834 -73.912585
5                  Kingsbridge  40.881687 -73.902818
6                  Marble Hill  40.876551 -73.910660
7                     Woodlawn  40.898273 -73.867315
8                      Norwood  40.877224 -73.879391
9               Williamsbridge  40.881039 -73.857446
10                  Baychester  40.866858 -73.835798
11              Pelham Parkway  40.857413 -73.854756
12                 City Island  40.847247 -73.786488
13                Bedford Park  40.870185 -73.885512
14          University Heights  40.855727 -73.910416
15              Morris Heights  40.847898 -73.919672
16                     Fordham  40.860997 -73.896427
17                East Tremont  40.842696 -73.887356
18                  West Farms  40.839475 -73.877745
19                High  Bridge  40.836623 -73.926102
20                     Melrose  40.819754 -73.909422
21                  Mott Haven  40.806239 -73.916100
22                 Port Morris  40.801664 -73.913221
23                    Longwood  40.815099 -73.895788
24                 Hunts Point  40.809730 -73.883315
25                  Morrisania  40.823592 -73.901506
26                   Soundview  40.821012 -73.865746
27                Clason Point  40.806551 -73.854144
28                 Throgs Neck  40.815109 -73.816350
29                Country Club  40.844246 -73.824099
30                 Parkchester  40.837938 -73.856003
31          Westchester Square  40.840619 -73.842194
32                    Van Nest  40.843608 -73.866299
33                 Morris Park  40.847549 -73.850402
34                     Belmont  40.857277 -73.888452
35              Spuyten Duyvil  40.881395 -73.917190
36             North Riverdale  40.908543 -73.904531
37                  Pelham Bay  40.850641 -73.832074
38               Schuylerville  40.826580 -73.826203
39              Edgewater Park  40.821986 -73.813885
40                 Castle Hill  40.819014 -73.848027
41                   Olinville  40.871371 -73.863324
42              Pelham Gardens  40.862966 -73.841612
43                   Concourse  40.834284 -73.915589
44                   Unionport  40.829774 -73.850535
45                    Edenwald  40.884561 -73.848083
46                   Bay Ridge  40.625801 -74.030621
47                 Bensonhurst  40.611009 -73.995180
48                 Sunset Park  40.645103 -74.010316
49                  Greenpoint  40.730201 -73.954241
50                   Gravesend  40.595260 -73.973471
51              Brighton Beach  40.576825 -73.965094
52              Sheepshead Bay  40.586890 -73.943186
53           Manhattan Terrace  40.614433 -73.957438
54                    Flatbush  40.636326 -73.958401
55               Crown Heights  40.670829 -73.943291
56               East Flatbush  40.641718 -73.936103
57                  Kensington  40.642382 -73.980421
58             Windsor Terrace  40.656946 -73.980073
59            Prospect Heights  40.676822 -73.964859
60                 Brownsville  40.663950 -73.910235
61                Williamsburg  40.707144 -73.958115
62                    Bushwick  40.698116 -73.925258
63          Bedford Stuyvesant  40.687232 -73.941785
64            Brooklyn Heights  40.695864 -73.993782
65                 Cobble Hill  40.687920 -73.998561
66             Carroll Gardens  40.680540 -73.994654
67                    Red Hook  40.676253 -74.012759
68                     Gowanus  40.673931 -73.994441
69                 Fort Greene  40.688527 -73.972906
70                  Park Slope  40.672321 -73.977050
71               Cypress Hills  40.682391 -73.876616
72               East New York  40.669926 -73.880699
73               Starrett City  40.647589 -73.879370
74                    Canarsie  40.635564 -

In [32]:
chicago_neighborhoods

Neighborhood   Latitude  Longitude
0                            Albany Park  41.968290 -87.723380
1                        Altgeld Gardens  41.654410 -87.602250
2                          Andersonville  41.980460 -87.668340
3                         Archer Heights  41.811540 -87.725560
4                          Armour Square  41.834580 -87.631890
5                                Ashburn  41.747850 -87.709950
6                        Ashburn Estates  41.941674 -88.198809
7                         Auburn Gresham  41.743190 -87.655040
8                            Avalon Park  41.745070 -87.588160
9                               Avondale  41.939250 -87.711250
10                      Avondale Gardens  41.980125 -87.780821
11                     Back of the Yards  41.810450 -87.662730
12                       Belmont Central  41.927460 -87.777340
13                       Belmont Gardens  41.937658 -87.831392
14                       Belmont Heights  41.937658 -87.831392
15                       Belmont Terrace  41.937658 -87.831392
16                               Beverly  41.715630 -87.672810
17                          Beverly View  41.732946 -87.670424
18                         Beverly Woods  41.683680 -87.680930
19                              Big Oaks  41.884250 -87.632450
20                              Boystown  41.921850 -87.697350
21                           Bowmanville  41.979728 -87.683936
22                              Brainerd  41.733180 -87.658120
23                             Brickyard  41.929190 -87.786000
24                            Bridgeport  41.837980 -87.650900
25                         Brighton Park  41.818610 -87.699480
26                           Bronzeville  41.823740 -87.623640
27                              Bucktown  41.917840 -87.673370
28                         Budlong Woods  41.912515 -87.672616
29                            Buena Park  41.958448 -87.652662
30                              Burnside  41.720300 -87.597450
31                         Cabrini–Green  41.871425 -87.653740
32                       Calumet Heights  41.733360 -87.577420
33                           Canaryville  41.816940 -87.640870
34                       Central Station  41.790652 -87.762193
35                               Chatham  41.741080 -87.613030
36                          Chicago Lawn  41.775430 -87.696340
37                             Chinatown  41.852790 -87.634950
38                      Chrysler Village  41.989300 -87.689910
39                        Clarendon Park  41.963070 -87.649920
40                         Clearing East  41.778090 -87.759780
41                         Clearing West  41.778090 -87.759780
42                 Cottage Grove Heights  41.700104 -87.608191
43                                Cragin  41.919550 -87.756010
44                             Crestline  41.744277 -87.725216
45                        Dearborn Homes  41.843090 -87.627830
46                         Dearborn Park  41.872270 -87.628690
47                          Douglas Park  41.863150 -87.696890
48                               Dunning  41.952740 -87.796510
49                          East Beverly  41.732946 -87.670424
50                          East Chatham  41.741080 -87.613030
51                    East Garfield Park  41.878500 -87.705520
52                        East Hyde Park  41.802391 -87.595045
53                           East Pilsen  41.857020 -87.657590
54                             East Side  41.712070 -87.530680
55                          East Village  41.899640 -87.672430
56                            Eden Green  42.011880 -87.699740
57                             Edgebrook  41.997320 -87.764230
58                             Edgewater  41.985710 -87.663460
59                       Edgewater Beach  41.987360 -87.655230
60                        Edgewater Glen  41.986200 -87.669397
61                           Edison Park  42.007890 -87.813990
62                             Englewood  41.779780 -87.645

# Part 2: getting relevant data from Foursquare API

Foursquare credentials

In [29]:
CLIENT_ID='ZPLPGG3VSLT050LEEIARCWZ5TTPS0BNNV42WU3EBQVKQAMTF'
CLIENT_SECRET='DX5SON5DXJKGOXZXMX3R2D4Z1SVCPJKHXXNE42MEZ3PSHGQL'
VERSION='20190903'

method to get nearby venues

In [30]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    LIMIT=100
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
            url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
            results = requests.get(url).json()["response"]['groups'][0]['items']
        
            venues_list.append([(
                name, 
                lat, 
                lng, 
                v['venue']['name'], 
                v['venue']['location']['lat'], 
                v['venue']['location']['lng'],  
                v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

getting nearby venues for the neighborhoods in the 2 cities

In [35]:
ny_venues=getNearbyVenues(names=ny_neighborhoods['Neighborhood'], latitudes=ny_neighborhoods['Latitude'], longitudes=ny_neighborhoods['Longitude'])
chicago_venues=getNearbyVenues(names=chicago_neighborhoods['Neighborhood'], latitudes=chicago_neighborhoods['Latitude'], longitudes=chicago_neighborhoods['Longitude'])

In [36]:
ny_venues

Neighborhood  Neighborhood Latitude  \
0                      Wakefield              40.894705   
1                      Wakefield              40.894705   
2                      Wakefield              40.894705   
3                      Wakefield              40.894705   
4                      Wakefield              40.894705   
5                      Wakefield              40.894705   
6                      Wakefield              40.894705   
7                      Wakefield              40.894705   
8                      Wakefield              40.894705   
9                      Wakefield              40.894705   
10                     Wakefield              40.894705   
11                    Co-op City              40.874294   
12                    Co-op City              40.874294   
13                    Co-op City              40.874294   
14                    Co-op City              40.874294   
15                    Co-op City              40.874294   
16                    Co-op City              40.874294   
17                    Co-op City              40.874294   
18                    Co-op City              40.874294   
19                    Co-op City              40.874294   
20                    Co-op City              40.874294   
21                    Co-op City              40.874294   
22                    Co-op City              40.874294   
23                    Co-op City              40.874294   
24                    Co-op City              40.874294   
25                    Co-op City              40.874294   
26                    Co-op City              40.874294   
27                    Co-op City              40.874294   
28                    Co-op City              40.874294   
29                    Co-op City              40.874294   
30                    Co-op City              40.874294   
31                    Co-op City              40.874294   
32                   Eastchester              40.887556   
33                   Eastchester              40.887556   
34                   Eastchester              40.887556   
35                   Eastchester              40.887556   
36                   Eastchester              40.887556   
37                   Eastchester              40.887556   
38                   Eastchester              40.887556   
39                   Eastchester              40.887556   
40                   Eastchester              40.887556   
41                   Eastchester              40.887556   
42                   Eastchester              40.887556   
43                   Eastchester              40.887556   
44                   Eastchester              40.887556   
45                   Eastchester              40.887556   
46                   Eastchester              40.887556   
47                   Eastchester              40.887556   
48                   Eastchester              40.887556   
49                   Eastchester              40.887556   
50                   Eastchester              40.887556   
51                   Eastchester              40.887556   
52                   Eastchester              40.887556   
53                   Eastchester              40.887556   
54                     Fieldston              40.895437   
55                     Fieldston              40.895437   
56                     Fieldston              40.895437   
57                     Fieldston              40.895437   
58                     Riverdale              40.890834   
59                     Riverdale              40.890834   
60                     Riverdale              40.890834   
61                     Riverdale              40.890834   
62                     Riverdale              40.890834   
63                     Riverdale              40.890834   
64                     Riverdale              40.890834   
65                     Riverdale              40.890834   
66                     Riverdale              40.890834   
67      

one hot encoding per venue type

In [148]:
ny_onehot = pd.get_dummies(ny_venues[['Venue Category']], prefix="", prefix_sep="")
ny_onehot['Neighborhood'] = ny_venues['Neighborhood']

chicago_onehot = pd.get_dummies(chicago_venues[['Venue Category']], prefix="", prefix_sep="")
chicago_onehot['Neighborhood'] = chicago_venues['Neighborhood']

# only keep categories present in both cities
fixed_columns = list(set(chicago_onehot.columns) & set(ny_onehot.columns))

ny_onehot = ny_onehot[fixed_columns]
ny_grouped = ny_onehot.groupby('Neighborhood').mean().reset_index()
ny_total = ny_venues.groupby(['Neighborhood']).size().reset_index(name='counts')
ny_data = pd.merge(ny_grouped, ny_total, on='Neighborhood')

chicago_onehot = chicago_onehot[fixed_columns]
chicago_grouped = chicago_onehot.groupby('Neighborhood').mean().reset_index()
chicago_total = chicago_venues.groupby(['Neighborhood']).size().reset_index(name='counts')
chicago_data = pd.merge(chicago_grouped, chicago_total, on='Neighborhood')

In [150]:
chicago_data.head()

Neighborhood  Sports Bar  Historic Site  Steakhouse  Beer Bar  \
0      Albany Park    0.000000       0.000000         0.0       0.0   
1  Altgeld Gardens    0.000000       0.000000         0.0       0.0   
2    Andersonville    0.000000       0.000000         0.0       0.0   
3   Archer Heights    0.000000       0.000000         0.0       0.0   
4    Armour Square    0.045455       0.045455         0.0       0.0   

   Roof Deck  Waterfront  German Restaurant  Antique Shop  BBQ Joint  \
0        0.0         0.0                0.0      0.000000        0.0   
1        0.0         0.0                0.0      0.000000        0.0   
2        0.0         0.0                0.0      0.017241        0.0   
3        0.0         0.0                0.0      0.000000        0.0   
4        0.0         0.0                0.0      0.000000        0.0   

   Insurance Office  Cafeteria  Doctor's Office  Laundromat  \
0               0.0        0.0              0.0         0.0   
1               0.0        0.0              0.0         0.0   
2               0.0        0.0              0.0         0.0   
3               0.0        0.0              0.0         0.0   
4               0.0        0.0              0.0         0.0   

   Outdoor Sculpture  Bus Line  Automotive Shop  Filipino Restaurant  \
0                0.0       0.0              0.0                  0.0   
1                0.0       0.0              0.0                  0.0   
2                0.0       0.0              0.0                  0.0   
3                0.0       0.0              0.0                  0.0   
4                0.0       0.0              0.0                  0.0   

   Vietnamese Restaurant  Asian Restaurant  Non-Profit  Playground  \
0                    0.0          0.000000         0.0    0.041667   
1                    0.0          0.000000         0.0    0.000000   
2                    0.0          0.017241         0.0    0.000000   
3                    0.0          0.000000         0.0    0.000000   
4                    0.0          0.045455         0.0    0.000000   

   Southern / Soul Food Restaurant  Salad Place  Bookstore  Harbor / Marina  \
0                         0.000000          0.0   0.000000              0.0   
1                         0.000000          0.0   0.000000              0.0   
2                         0.017241          0.0   0.017241              0.0   
3                         0.000000          0.0   0.000000              0.0   
4                         0.000000          0.0   0.000000              0.0   

   Building  Climbing Gym  Japanese Restaurant  Design Studio  \
0       0.0           0.0                  0.0            0.0   
1       0.0           0.0                  0.0            0.0   
2       0.0           0.0                  0.0            0.0   
3       0.0           0.0                  0.0            0.0   
4       0.0           0.0                  0.0            0.0   

   Basketball Court  Bike Trail  Tennis Court  Shoe Repair  Board Shop  \
0               0.0         0.0           0.0          0.0         0.0   
1               0.0         0.0           0.0          0.0         0.0   
2               0.0         0.0           0.0          0.0         0.0   
3               0.0         0.0           0.0          0.0         0.0   
4               0.0         0.0           0.0          0.0         0.0   

   Shop & Service  Hotpot Restaurant  Restaurant  Health Food Store  \
0             0.0                0.0    0.000000                0.0   
1             0.0                0.0    0.000000                0.0   
2             0.0                0.0    0.017241                0.0   
3             0.0                0.0    0.000000                0.0   
4             0.0                0.0    0.000000                0.0   

   Korean Restaurant  Turkish Restaurant  Cupcake Shop  Scenic Lookout  \
0           0.041667                 0.0           0.0             0.0   
1           0.000000       

In [151]:
ny_data.head()

Neighborhood  Sports Bar  Historic Site  Steakhouse  Beer Bar  Roof Deck  \
0       Allerton    0.000000            0.0         0.0       0.0        0.0   
1       Annadale    0.090909            0.0         0.0       0.0        0.0   
2  Arden Heights    0.000000            0.0         0.0       0.0        0.0   
3      Arlington    0.000000            0.0         0.0       0.0        0.0   
4       Arrochar    0.000000            0.0         0.0       0.0        0.0   

   Waterfront  German Restaurant  Antique Shop  BBQ Joint  Insurance Office  \
0         0.0                0.0           0.0        0.0               0.0   
1         0.0                0.0           0.0        0.0               0.0   
2         0.0                0.0           0.0        0.0               0.0   
3         0.0                0.0           0.0        0.0               0.0   
4         0.0                0.0           0.0        0.0               0.0   

   Cafeteria  Doctor's Office  Laundromat  Outdoor Sculpture  Bus Line  \
0        0.0              0.0         0.0                0.0       0.0   
1        0.0              0.0         0.0                0.0       0.0   
2        0.0              0.0         0.0                0.0       0.0   
3        0.0              0.0         0.0                0.0       0.0   
4        0.0              0.0         0.0                0.0       0.0   

   Automotive Shop  Filipino Restaurant  Vietnamese Restaurant  \
0              0.0                  0.0                    0.0   
1              0.0                  0.0                    0.0   
2              0.0                  0.0                    0.0   
3              0.0                  0.0                    0.0   
4              0.0                  0.0                    0.0   

   Asian Restaurant  Non-Profit  Playground  Southern / Soul Food Restaurant  \
0               0.0         0.0    0.032258                              0.0   
1               0.0         0.0    0.000000                              0.0   
2               0.0         0.0    0.000000                              0.0   
3               0.0         0.0    0.000000                              0.0   
4               0.0         0.0    0.000000                              0.0   

   Salad Place  Bookstore  Harbor / Marina  Building  Climbing Gym  \
0          0.0        0.0              0.0       0.0           0.0   
1          0.0        0.0              0.0       0.0           0.0   
2          0.0        0.0              0.0       0.0           0.0   
3          0.0        0.0              0.0       0.0           0.0   
4          0.0        0.0              0.0       0.0           0.0   

   Japanese Restaurant  Design Studio  Basketball Court  Bike Trail  \
0                  0.0            0.0               0.0         0.0   
1                  0.0            0.0               0.0         0.0   
2                  0.0            0.0               0.0         0.0   
3                  0.0            0.0               0.0         0.0   
4                  0.0            0.0               0.0         0.0   

   Tennis Court  Shoe Repair  Board Shop  Shop & Service  Hotpot Restaurant  \
0           0.0          0.0         0.0             0.0                0.0   
1           0.0          0.0         0.0             0.0                0.0   
2           0.0          0.0         0.0             0.0                0.0   
3           0.0          0.0         0.0             0.0                0.0   
4           0.0          0.0         0.0             0.0                0.0   

   Restaurant  Health Food Store  Korean Restaurant  Turkish Restaurant  \
0    0.000000                0.0                0.0                 0.0   
1    0.090909                0.0                0.0                 0.0   
2    0.000000                0.0                0.0                 0.0   
3    0.000000                0.0                0.0                 0.0   
4    0.000000              

only keep neighborhoods with more than 20 venues

In [152]:
chicago_30 = chicago_data[chicago_data['counts'] > 30]
ny_30 = ny_data[ny_data['counts'] > 30]

In [153]:
chicago_30.set_index('Neighborhood', inplace=True)
ny_30.set_index('Neighborhood', inplace=True)

In [154]:
ny_30.head()

Sports Bar  Historic Site  Steakhouse  Beer Bar  Roof Deck  \
Neighborhood                                                                    
Allerton             0.000000           0.00        0.00       0.0        0.0   
Astoria              0.000000           0.00        0.00       0.0        0.0   
Bath Beach           0.000000           0.00        0.00       0.0        0.0   
Battery Park City    0.000000           0.01        0.01       0.0        0.0   
Bay Ridge            0.011905           0.00        0.00       0.0        0.0   

                   Waterfront  German Restaurant  Antique Shop  BBQ Joint  \
Neighborhood                                                                
Allerton                  0.0           0.000000           0.0       0.00   
Astoria                   0.0           0.000000           0.0       0.01   
Bath Beach                0.0           0.018868           0.0       0.00   
Battery Park City         0.0           0.000000           0.0       0.02   
Bay Ridge                 0.0           0.000000           0.0       0.00   

                   Insurance Office  Cafeteria  Doctor's Office  Laundromat  \
Neighborhood                                                                  
Allerton                        0.0        0.0              0.0         0.0   
Astoria                         0.0        0.0              0.0         0.0   
Bath Beach                      0.0        0.0              0.0         0.0   
Battery Park City               0.0        0.0              0.0         0.0   
Bay Ridge                       0.0        0.0              0.0         0.0   

                   Outdoor Sculpture  Bus Line  Automotive Shop  \
Neighborhood                                                      
Allerton                         0.0       0.0              0.0   
Astoria                          0.0       0.0              0.0   
Bath Beach                       0.0       0.0              0.0   
Battery Park City                0.0       0.0              0.0   
Bay Ridge                        0.0       0.0              0.0   

                   Filipino Restaurant  Vietnamese Restaurant  \
Neighborhood                                                    
Allerton                           0.0               0.000000   
Astoria                            0.0               0.000000   
Bath Beach                         0.0               0.000000   
Battery Park City                  0.0               0.000000   
Bay Ridge                          0.0               0.011905   

                   Asian Restaurant  Non-Profit  Playground  \
Neighborhood                                                  
Allerton                   0.000000         0.0    0.032258   
Astoria                    0.000000         0.0    0.000000   
Bath Beach                 0.018868         0.0    0.000000   
Battery Park City          0.000000         0.0    0.020000   
Bay Ridge                  0.000000         0.0    0.023810   

                   Southern / Soul Food Restaurant  Salad Place  Bookstore  \
Neighborhood                                                                 
Allerton                                       0.0         0.00   0.000000   
Astoria                                        0.0         0.01   0.000000   
Bath Beach                                     0.0         0.00   0.000000   
Battery Park City                              0.0         0.00   0.000000   
Bay Ridge                                      0.0         0.00   0.011905   

                   Harbor / Marina  Building  Climbing Gym  \
Neighborhood                                                 
Allerton                       0.0      0.00           0.0   
Astoria                        0.0      0.00           0.0   
Bath Beach                     0.0      0.00           0.0   
Battery Park City              0.0      0.01           0.0   
Bay Ridge                      0.0      0.00           0.0   

       

separating x and y (the relative amount of pizzerias is the value to be predicted y)

In [155]:
chicago_Y = chicago_30['Pizza Place']
chicago_X = chicago_30
del chicago_X['Pizza Place']

In [156]:
chicago_counts=chicago_X['counts']

# Part 3: training the model on Chicago

normalization

In [157]:
from sklearn import preprocessing
X = preprocessing.StandardScaler().fit(chicago_X).transform(chicago_X.astype(float))

separating train and test data

In [161]:
from sklearn.model_selection import train_test_split
x_train, x_test, y_train, y_test = train_test_split (X, chicago_Y, test_size = 0.3, random_state = 0)

find best K for a K nearest neighbors regressor, weighting them with the distance to the predictor

In [162]:
from sklearn.neighbors import KNeighborsRegressor
from sklearn.metrics import mean_squared_error

Ks = 10
mse = np.zeros((Ks-1))
for n in range(1,Ks):
    neigh = KNeighborsRegressor(n_neighbors = n, weights='distance').fit(x_train,y_train)
    yhat=neigh.predict(x_test)
    mse[n-1] = mean_squared_error(y_test, yhat)
print ("best K is %d with MSE %f" % (mse.argmin()+1, mse.min()))

best K is 5 with MSE 0.000277


In [163]:
meanY = y_test.mean()
print ('the mean frequency of pizza places in the test set is %f, so the MSE is %f %% of the mean frequency'
      % (meanY, 100*mse.min()/meanY))

the mean frequency of pizza places in the test set is 0.033702, so the MSE is 0.821882 % of the mean frequency


which means the model has great accuracy

In [164]:
myModel = KNeighborsRegressor(n_neighbors=5, weights='distance').fit(X,chicago_Y)

# Part 4: predictions on the new city and comparisons

prepare the dataset

In [165]:
ny_Y = ny_30['Pizza Place']
ny_X = ny_30
del ny_X['Pizza Place']

ny_counts=ny_X['counts']

from sklearn import preprocessing
X = preprocessing.StandardScaler().fit(ny_X).transform(ny_X.astype(float))

predict

In [166]:
y_hat = myModel.predict(X)

create dataset with all useful information

In [171]:
ny_Y = pd.DataFrame(ny_Y)

In [178]:
NY_final = pd.merge(ny_total, ny_Y, on='Neighborhood')

In [187]:
NY_final['predicted'] = y_hat

In [188]:
NY_final

Neighborhood  counts  Pizza Place  predicted
0                     Allerton      31     0.161290   0.013197
1                      Astoria     100     0.020000   0.030033
2                   Bath Beach      53     0.037736   0.040578
3            Battery Park City     100     0.020000   0.019031
4                    Bay Ridge      84     0.047619   0.033088
5                  Bay Terrace      49     0.020408   0.027226
6                      Bayside      75     0.040000   0.004086
7                 Bedford Park      35     0.085714   0.048918
8                      Belmont     100     0.080000   0.011375
9                  Bensonhurst      32     0.031250   0.040801
10                 Boerum Hill      89     0.000000   0.045017
11              Brighton Beach      44     0.000000   0.048549
12            Brooklyn Heights     100     0.030000   0.004113
13                  Bulls Head      39     0.128205   0.041334
14                    Bushwick      73     0.054795   0.029539
15               Carnegie Hill     100     0.060000   0.042491
16             Carroll Gardens     100     0.040000   0.045621
17              Central Harlem      45     0.022222   0.037929
18                  Charleston      31     0.032258   0.027467
19                     Chelsea     104     0.009615   0.040711
20                   Chinatown     100     0.010000   0.032506
21                   City Line      41     0.024390   0.044628
22                Civic Center     100     0.000000   0.015187
23                     Clinton     100     0.010000   0.000000
24                Clinton Hill      95     0.052632   0.042496
25                 Cobble Hill     100     0.040000   0.021353
26               College Point      40     0.050000   0.043406
27           Concourse Village      32     0.031250   0.041115
28                 Ditmas Park      47     0.042553   0.039612
29                    Downtown     100     0.020000   0.000000
30                       Dumbo      86     0.023256   0.034431
31                 East Harlem      46     0.021739   0.024910
32                East Village     100     0.040000   0.031897
33           East Williamsburg      68     0.000000   0.043245
34                    Elmhurst      39     0.025641   0.026006
35                 Eltingville      35     0.085714   0.039695
36                Far Rockaway      32     0.093750   0.045033
37          Financial District     100     0.040000   0.000000
38                    Flatiron     100     0.000000   0.016890
39                    Flushing      57     0.000000   0.023191
40                     Fordham      91     0.043956   0.034769
41                Forest Hills      38     0.052632   0.044046
42                 Fort Greene      74     0.027027   0.000000
43               Fort Hamilton      71     0.028169   0.025015
44                Fulton Ferry      62     0.032258   0.030483
45                  Georgetown      31     0.032258   0.049227
46                     Gowanus      69     0.028986   0.024397
47                    Gramercy     100     0.040000   0.018894
48                   Gravesend      32     0.062500   0.025607
49                  Greenpoint     100     0.050000   0.004037
50           Greenwich Village     100     0.010000   0.030251
51            Hamilton Heights      62     0.080645   0.037317
52                High  Bridge      33     0.090909   0.048353
53                   Homecrest      43     0.046512   0.040112
54                Howard Beach      37     0.000000   0.052721
55                Hudson Yards      78     0.000000   0.015338
56               Hunters Point      75     0.013333   0.048461
57                      Inwood      60     0.050000   0.044298
58             Jackson Heights      82     0.024390   0.026966
59              Jamaica Center      44     0.045455   0.041269
60                  Kensington      39     0.051282   0.040496
61                 Kew Gardens      47     0.042553   0.034005
62                 Kingsbridge      72     0.1111

accuracy score

In [189]:
meanY = ny_Y.mean()
mse = mean_squared_error (ny_Y, y_hat)
print ('the mean frequency of pizza places in the ny set is %f, so the MSE is %f %% of the mean frequency'
      % (meanY, 100*mse.min()/meanY))

the mean frequency of pizza places in the ny set is 0.039989, so the MSE is 2.818573 % of the mean frequency


add differences between prediction and actual frequency to the dataset

In [190]:
NY_final['Frequency difference']=NY_final['predicted']-NY_final['Pizza Place']
NY_final['Absolute difference']=NY_final['Frequency difference']*NY_final['counts']

In [191]:
NY_final

Neighborhood  counts  Pizza Place  predicted  \
0                     Allerton      31     0.161290   0.013197   
1                      Astoria     100     0.020000   0.030033   
2                   Bath Beach      53     0.037736   0.040578   
3            Battery Park City     100     0.020000   0.019031   
4                    Bay Ridge      84     0.047619   0.033088   
5                  Bay Terrace      49     0.020408   0.027226   
6                      Bayside      75     0.040000   0.004086   
7                 Bedford Park      35     0.085714   0.048918   
8                      Belmont     100     0.080000   0.011375   
9                  Bensonhurst      32     0.031250   0.040801   
10                 Boerum Hill      89     0.000000   0.045017   
11              Brighton Beach      44     0.000000   0.048549   
12            Brooklyn Heights     100     0.030000   0.004113   
13                  Bulls Head      39     0.128205   0.041334   
14                    Bushwick      73     0.054795   0.029539   
15               Carnegie Hill     100     0.060000   0.042491   
16             Carroll Gardens     100     0.040000   0.045621   
17              Central Harlem      45     0.022222   0.037929   
18                  Charleston      31     0.032258   0.027467   
19                     Chelsea     104     0.009615   0.040711   
20                   Chinatown     100     0.010000   0.032506   
21                   City Line      41     0.024390   0.044628   
22                Civic Center     100     0.000000   0.015187   
23                     Clinton     100     0.010000   0.000000   
24                Clinton Hill      95     0.052632   0.042496   
25                 Cobble Hill     100     0.040000   0.021353   
26               College Point      40     0.050000   0.043406   
27           Concourse Village      32     0.031250   0.041115   
28                 Ditmas Park      47     0.042553   0.039612   
29                    Downtown     100     0.020000   0.000000   
30                       Dumbo      86     0.023256   0.034431   
31                 East Harlem      46     0.021739   0.024910   
32                East Village     100     0.040000   0.031897   
33           East Williamsburg      68     0.000000   0.043245   
34                    Elmhurst      39     0.025641   0.026006   
35                 Eltingville      35     0.085714   0.039695   
36                Far Rockaway      32     0.093750   0.045033   
37          Financial District     100     0.040000   0.000000   
38                    Flatiron     100     0.000000   0.016890   
39                    Flushing      57     0.000000   0.023191   
40                     Fordham      91     0.043956   0.034769   
41                Forest Hills      38     0.052632   0.044046   
42                 Fort Greene      74     0.027027   0.000000   
43               Fort Hamilton      71     0.028169   0.025015   
44                Fulton Ferry      62     0.032258   0.030483   
45                  Georgetown      31     0.032258   0.049227   
46                     Gowanus      69     0.028986   0.024397   
47                    Gramercy     100     0.040000   0.018894   
48                   Gravesend      32     0.062500   0.025607   
49                  Greenpoint     100     0.050000   0.004037   
50           Greenwich Village     100     0.010000   0.030251   
51            Hamilton Heights      62     0.080645   0.037317   
52                High  Bridge      33     0.090909   0.048353   
53                   Homecrest      43     0.046512   0.040112   
54                Howard Beach      37     0.000000   0.052721   
55                Hudson Yards      78     0.000000   0.015338   
56               Hunters Point      75     0.013333   0.048461   
57                      Inwood      60     0.050000   0.044298   
58             Jackson Heights      82     0.024390   0.026966   
59              Jamaica Center      44     0.045455   0.04

look for a bias in the predictions, which could be due to differences between the two cities

In [192]:
print ('The mean absolute difference between predicted amount of Pizza Places and actual amount is: %f' 
       %NY_final['Absolute difference'].mean())

The mean absolute difference between predicted amount of Pizza Places and actual amount is: -0.494184


This means New York tends to have a slightly higher relative amount of Pizza Places.
It's not a big problem: it means that the predictions are a bit pessimistic.

# Part 6: visualize the results on a Folium map

add back the coordinates to the dataset

In [194]:
NY_final.set_index('Neighborhood', inplace=True)

In [195]:
ny_neighborhoods.set_index('Neighborhood', inplace=True)

In [199]:
NY = pd.merge(ny_neighborhoods, NY_final, on='Neighborhood', how='inner')

In [200]:
NY

Latitude  Longitude  counts  Pizza Place  \
Neighborhood                                                           
Kingsbridge                40.881687 -73.902818      72     0.111111   
Bedford Park               40.870185 -73.885512      35     0.085714   
Fordham                    40.860997 -73.896427      91     0.043956   
High  Bridge               40.836623 -73.926102      33     0.090909   
Parkchester                40.837938 -73.856003      38     0.078947   
Westchester Square         40.840619 -73.842194      32     0.062500   
Belmont                    40.857277 -73.888452     100     0.080000   
Pelham Bay                 40.850641 -73.832074      44     0.000000   
Bay Ridge                  40.625801 -74.030621      84     0.047619   
Bensonhurst                40.611009 -73.995180      32     0.031250   
Sunset Park                40.645103 -74.010316      34     0.088235   
Greenpoint                 40.730201 -73.954241     100     0.050000   
Gravesend                  40.595260 -73.973471      32     0.062500   
Brighton Beach             40.576825 -73.965094      44     0.000000   
Kensington                 40.642382 -73.980421      39     0.051282   
Prospect Heights           40.676822 -73.964859      83     0.024096   
Williamsburg               40.707144 -73.958115      33     0.030303   
Bushwick                   40.698116 -73.925258      73     0.054795   
Brooklyn Heights           40.695864 -73.993782     100     0.030000   
Cobble Hill                40.687920 -73.998561     100     0.040000   
Carroll Gardens            40.680540 -73.994654     100     0.040000   
Red Hook                   40.676253 -74.012759      50     0.020000   
Gowanus                    40.673931 -73.994441      69     0.028986   
Fort Greene                40.688527 -73.972906      74     0.027027   
Park Slope                 40.672321 -73.977050      71     0.042254   
Bath Beach                 40.599519 -73.998752      53     0.037736   
Clinton Hill               40.693229 -73.967843      95     0.052632   
Downtown                   40.690844 -73.983463     100     0.020000   
Boerum Hill                40.685683 -73.983748      89     0.000000   
Prospect Lefferts Gardens  40.658420 -73.954899      52     0.057692   
City Line                  40.678570 -73.867976      41     0.024390   
Prospect Park South        40.647009 -73.962613      50     0.080000   
Georgetown                 40.623845 -73.916075      31     0.032258   
East Williamsburg          40.708492 -73.938858      68     0.000000   
North Side                 40.714823 -73.958809     100     0.040000   
South Side                 40.710861 -73.958001     100     0.040000   
Fort Hamilton              40.614768 -74.031979      71     0.028169   
Chinatown                  40.715618 -73.994279     100     0.010000   
Washington Heights         40.851903 -73.936900      88     0.011364   
Inwood                     40.867684 -73.921210      60     0.050000   
Hamilton Heights           40.823604 -73.949688      62     0.080645   
Manhattanville             40.816934 -73.957385      42     0.000000   
Central Harlem             40.815976 -73.943211      45     0.022222   
East Harlem                40.792249 -73.944182      46     0.021739   
Upper East Side            40.775639 -73.960508     100     0.020000   
Yorkville                  40.775930 -73.947118     100     0.050000   
Lenox Hill                 40.768113 -73.958860     100     0.050000   
Upper West Side            40.787658 -73.977059     100     0.020000   
Lincoln Square             40.773529 -73.985338     100     0.000000   
Clinton                    40.759101 -73.996119     100     0.010000   
Midtown                    40.754691 -73.981669     100     0.010000   
Murray Hill                40.748303 -73.978332     146     0.013699   
Murray Hill                40.764126 -73.812763     146     0.013699   
Chelsea                    40.744035 -74.003116     104     0.009615

visualize

In [201]:
import folium

In [207]:
NY.reset_index(inplace=True)

In [226]:
venues_map = folium.Map(location=[40.730610, -73.935242], zoom_start=10)

def getColor (difference):
    if difference < -1:
        return 'darkred'
    elif difference < 0:
        return 'red'
    elif difference < 1:
        return 'orange'
    elif difference < 2:
        return 'lightgreen'
    else:
        return 'darkgreen'

for i in range (0, len(NY)):
    folium.CircleMarker([NY.loc[i, 'Latitude'], NY.loc[i, 'Longitude']], 
                        radius=5, color=getColor(NY.loc[i, 'Absolute difference']),
                        popup='{} : there seems to be place for {} Pizza places more'.format(NY.loc[i, 'Neighborhood'], NY.loc[i, 'Absolute difference']),
                        fill = True, fill_color = getColor(NY.loc[i, 'Absolute difference']), fill_opacity = 0.6).add_to(venues_map)

In [227]:
venues_map

find best neighborhoods to start a pizza place in New York

In [228]:
NY.sort_values(by='Absolute difference', axis=0, ascending=False, inplace=True)

In [229]:
NY

Neighborhood   Latitude  Longitude  counts  Pizza Place  \
28                 Boerum Hill  40.685683 -73.983748      89     0.000000   
54                     Chelsea  40.594726 -74.189560     104     0.009615   
53                     Chelsea  40.744035 -74.003116     104     0.009615   
33           East Williamsburg  40.708492 -73.938858      68     0.000000   
104              Hunters Point  40.743414 -73.953868      75     0.013333   
99               Midtown South  40.748510 -73.988713     100     0.000000   
38          Washington Heights  40.851903 -73.936900      88     0.011364   
60                        Soho  40.722184 -74.000657     100     0.010000   
7                   Pelham Bay  40.850641 -73.832074      44     0.000000   
37                   Chinatown  40.715618 -73.994279     100     0.010000   
13              Brighton Beach  40.576825 -73.965094      44     0.000000   
55           Greenwich Village  40.726933 -73.999914     100     0.010000   
52                 Murray Hill  40.764126 -73.812763     146     0.013699   
51                 Murray Hill  40.748303 -73.978332     146     0.013699   
71                Howard Beach  40.654225 -73.838138      37     0.000000   
107                   Flatiron  40.739673 -73.990947     100     0.000000   
98                Civic Center  40.715229 -74.005415     100     0.000000   
68                    Woodside  40.746349 -73.901842      78     0.038462   
58                     Tribeca  40.721522 -74.010683     100     0.010000   
15            Prospect Heights  40.676822 -73.964859      83     0.024096   
74                    Flushing  40.764454 -73.831773      57     0.000000   
114               Hudson Yards  40.756658 -74.000111      78     0.000000   
108          Sunnyside Gardens  40.745652 -73.918193     100     0.030000   
21                    Red Hook  40.676253 -74.012759      50     0.020000   
67                     Astoria  40.768509 -73.915654     100     0.020000   
110                      Dumbo  40.703176 -73.988753      86     0.023256   
41              Manhattanville  40.816934 -73.957385      42     0.000000   
91               West Brighton  40.631879 -74.107182      40     0.025000   
30                   City Line  40.678570 -73.867976      41     0.024390   
61                West Village  40.734434 -74.006180     100     0.020000   
42              Central Harlem  40.815976 -73.943211      45     0.022222   
84                 Little Neck  40.770826 -73.738898      52     0.038462   
106                 Tudor City  40.746917 -73.971219      81     0.037037   
20             Carroll Gardens  40.680540 -73.994654     100     0.040000   
32                  Georgetown  40.623845 -73.916075      31     0.032258   
16                Williamsburg  40.707144 -73.958115      33     0.030303   
87                 Bay Terrace  40.782843 -73.776802      49     0.020408   
88                 Bay Terrace  40.553988 -74.139166      49     0.020408   
101          Concourse Village  40.824780 -73.915847      32     0.031250   
9                  Bensonhurst  40.611009 -73.995180      32     0.031250   
97                        Noho  40.723259 -73.988434     100     0.030000   
89              Rockaway Beach  40.582802 -73.822361      57     0.035088   
69             Jackson Heights  40.751981 -73.882821      82     0.024390   
25                  Bath Beach  40.599519 -73.998752      53     0.037736   
43                 East Harlem  40.792249 -73.944182      46     0.021739   
70                    Elmhurst  40.744049 -73.881656      39     0.025641   
48              Lincoln Square  40.773529 -73.985338     100     0.000000   
65           Battery Park City  40.711932 -74.016869     100     0.020000   
109               Fulton Ferry  40.703281 -73.995508      62     0.032258   
93                 Ditmas Park  40.643675 -73.961013      47     0.042553   
94                  Charleston  40.530531 -74.232158      31     0.032258   
85            